In [1]:
import scipy.io.wavfile as scp
import numpy as np
import pandas as pd
import math
import pyperclip
import statistics

In [2]:
def reverse_string(input_string):
    return input_string[::-1]

In [3]:
payFilename = r'G:\My Drive\Novice Team II\group 1\Dataset\Payload\payload1.txt'
### Embedding 

In [4]:
## Step 1 - Read audio and sample to 16-bit and normalize audio sample
wavFilename = r"G:\My Drive\Novice Team II\group 1\Dataset\Audio\data3_mono.wav"
samplerate, audiodata = scp.read(wavFilename)
audiodata = audiodata.astype(np.int32)
print("\nEmbedding Process~~~\n")
print("Length of Audio Sample: ", len(audiodata))
print("ori aud : ",audiodata)

#print("ori aud [maxo] : ",audiodata[204])
normaudiodata = [x + 32768 for x in audiodata]
#print("Audio Sample [awal] : ", normaudiodata[0])
#print("Audio Sample [akhir] : ", normaudiodata[len(normaudiodata)-1])
#print(normaudiodata)
#print("Audio Sample [i] : ", normaudiodata[132300])


Embedding Process~~~

Length of Audio Sample:  132299
ori aud :  [  -758  -2047     83 ... -22364 -20958 -19248]
ori aud :  -493
ori aud :  61
ori aud :  -1758
ori aud :  -333
ori aud :  568
ori aud :  1064
ori aud :  5289
ori aud :  2717
ori aud :  2959
normalized Sample [i] :  32275
normalized Sample [i] :  32829
normalized Sample [i] :  31010
normalized Sample [i] :  32435
normalized Sample [i] :  33336
normalized Sample [i] :  33832
normalized Sample [i] :  38057
normalized Sample [i] :  35485
normalized Sample [i] :  35727


In [5]:
## secret bits
temp = None
secret_bits = []
with open(payFilename, "r") as file1:
    temp = file1.read().replace("\t", "")
for i in temp:
    secret_bits.append(int(i))

#### PRE INTERPOLATION

In [6]:
## PRE INTERPOLATION
s_normaudiodata = normaudiodata.copy()
p_interpolasi = np.resize(normaudiodata, (len(normaudiodata)))

for i in range(len(p_interpolasi)-1):
    if normaudiodata[i] <= normaudiodata[i+1]:
        p_interpolasi[i] = math.floor((normaudiodata[i] + normaudiodata[i+1])/2)
    else:
        p_interpolasi[i] = math.ceil((normaudiodata[i] + normaudiodata[i+1])/2)

## Estimated maximum capacity of each i-th sample in bits
B = [0 for i in range (len(p_interpolasi))]
for i in range (len(B)):
    if abs(normaudiodata[i]-p_interpolasi[i]) > 0 :
        B[i] = math.floor(math.log(abs(normaudiodata[i]-p_interpolasi[i]),2))
    else :
        B[i]= 0

res = 0
for i in range (len(B)):
    res += B[i]
print("maxxx : ", res)

## BN and BA
BA = statistics.mean(B)
print("[Info] Average bit available for embedding in each sample: ",BA)
BN = len(secret_bits)/len(p_interpolasi)
print(BN)


## Bb and Bt
Bt = max(math.ceil(BN), math.floor(BA))
Bb = min(math.ceil(BN), math.floor(BA))

## B'
if Bb > 1 :
    for i in range (len(B)):
        if B[i] >= Bt :
            B[i] = Bb
        elif (Bb-1) <= B[i] and B[i] < Bt :
            B[i] = Bb - 1
        elif B[i] < (Bb - 1) :
            B[i] = B[i]

elif Bb == 1 :
    for i in range (len(B)) :
        if B[i] >= Bb :
            B[i] = Bb
        else :
            B[i] = 0

ress = 0
for i in range (len(B)):
    ress += B[i]
print("maxxi : ", ress)
print("Maximum bit capacity : ",sum(B))
## modified interpolation
for i in range (len(p_interpolasi)-1) :
    if s_normaudiodata[i] <= normaudiodata[i+1] :
        p_interpolasi[i] = math.floor((((2 ** B[i])-1) * s_normaudiodata[i]) + (normaudiodata[i+1])) / (2 ** B[i])
    else : 
        p_interpolasi[i] = math.ceil((((2 ** B[i])-1) * s_normaudiodata[i]) + (normaudiodata[i+1])) / (2 ** B[i])

print("pra interpolasi : ", p_interpolasi[80])
print("pra interpolasi : ", p_interpolasi[81])
print("pra interpolasi : ", p_interpolasi[82])
print("pra interpolasi : ", p_interpolasi[83])
print("pra interpolasi : ", p_interpolasi[84])
print("pra interpolasi : ", p_interpolasi[85])
print("pra interpolasi : ", p_interpolasi[86])
print("pra interpolasi : ", p_interpolasi[87])
print("pra interpolasi : ", p_interpolasi[88])

print("panjang pra interpolasi : ", len(p_interpolasi))
audiodataa = [x - 32768 for x in p_interpolasi]
interpolasi = np.resize(p_interpolasi, ((len(p_interpolasi)*2)-1))




maxxx :  1261583
[Info] Average bit available for embedding in each sample:  9.53584683179767
0.0075586361196985615
maxxi :  132207
Maximum bit capacity :  132207
pra interpolasi :  32552
pra interpolasi :  31919
pra interpolasi :  31722
pra interpolasi :  32885
pra interpolasi :  33584
pra interpolasi :  35944
pra interpolasi :  36771
pra interpolasi :  35606
pra interpolasi :  33814
panjang pra interpolasi :  132299


In [7]:
x = 0

for i in range(len(interpolasi)):
    # Even Sample (Original Sample)
    if i % 2 == 0:
        interpolasi[i] = p_interpolasi[int(i/2)]
    # Odd Sample (Interpolation)
    else:
        interpolasi[i] = math.floor((p_interpolasi[int((i-1)/2)]+p_interpolasi[i-x])/2)
        x+=1

interpolated = [x for x in interpolasi]

264597
BEFORE EMBEDDING 
Interpolation Sample [160] :  32552
Interpolation Sample [1000+i] :  32235
Interpolation Sample [1000+i] :  31919
Interpolation Sample [1000+i] :  31820
Interpolation Sample [1000+i] :  31722
Interpolation Sample [1000+i] :  32303
Interpolation Sample [1000+i] :  32885
Interpolation Sample [1000+i] :  33234
Interpolation Sample [1000+i] :  33584
Interpolation Sample [1000+i] :  34764
Interpolation Sample [1000+i] :  35944
Interpolation Sample [1000+i] :  36357
Interpolation Sample [1000+i] :  36771
Interpolation Sample [1000+i] :  36188
Interpolation Sample [1000+i] :  35606
Interpolation Sample [1000+i] :  34710
Interpolation Sample [1000+i] :  33814


In [8]:
## Save Interpolation Audio
interpolasi = [x - 32768 for x in interpolasi]
scp.write('G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\interadmod.wav', samplerate, np.array(interpolasi, dtype=np.int16))

In [9]:
## Step 3 - Find variable C
duration = len(interpolasi) / samplerate
print("Interad duration : ",duration)
C = (duration * 1000)/((len(interpolasi))*2)
print("C = ", C)

Interad duration :  5.999931972789116
C =  0.011337868480725625


In [10]:
## Steps 4 and 5 - Embedding Process
with open(payFilename, 'r') as file:
    payload = file.read()
payload = payload.replace('\t', '')
nSpace = 0

interpolasi = [x + 32768 for x in interpolasi]
truekey = ''
keyo = ''

ganjil = 0
genap = 0
miss = 0
iterasi = 0
maks = 0 

print("i : ",i)
print("Interpolation Length : ", len(interpolasi))
i=0
for i in range(len(interpolasi)-1):
    iterasi+=1
    # Step 5 - Odd number (Interpolation)
    if i % 2 != 0:
        key = ''
        ganjil+=1
        if abs(N) == 0:
            key += '00'
        for x in range(abs(N)):
            if len(pn) < abs(N) and x == len(pn):
                break
            r = interpolasi[i] % 2 
            if int(pn[x]) > 0:
                key += '11'
                interpolasi[i] += 1
            elif int(pn[x]) == 0:
                key += '10'
                interpolasi[i] -= 1     
        reversed_key = reverse_string(key)
        #if i == 161 :
        #    print(reversed_key)  
        truekey += reversed_key
        if i > 159 and i < 177 :
            keyo += reversed_key
            print("true key : ", keyo)

        if nSpace > len(payload) or nSpace == len(payload):
            break
    # Step 4 - Even number except last (Original)
    elif i < len(interpolasi):
        genap+=1
        d = math.sqrt((i+1-(i+2))**2+(interpolasi[i]-interpolasi[i+1])**2)
        N = math.floor(math.log2(C * d))
        #print("===")
        #print(N)
        #print(i)
        if N == 0:
            pn = 0
            nSpace+=abs(N)
        elif nSpace < len(payload) and (nSpace + abs(N) - 1) < len(payload):
            pn = payload[nSpace:(nSpace+abs(N))]
            nSpace+=abs(N)
        elif nSpace + abs(N) > len(payload):
            pn = payload[nSpace:len(payload)]
            nSpace+=abs(N)
        #print(pn)
        #print("===")
        if i > 159 and i < 177 :
            print("===")
            print("i : ", i)
            print("inter i : ", interpolasi[i])
            print("inter i+1 : ", interpolasi[i+1])
            print("N : ", N)
            print("Payload : ", pn)
            
       
    else :
        miss+=1
print(f"Ganjil : {ganjil},Genap : {genap}, Miss : {miss}, Iterasi : {iterasi}")
print("Length of Key : ", len(truekey))

print("Total space : ", nSpace)
print(interpolasi[161])



#print("Interpolation Sample [maks + 1] : ", interpolasi[id+1])
#print("Interpolation Sample [i*2] : ", interpolasi[200])




i :  264596
Interpolation Length :  264597
===
i :  160
inter i :  32552
inter i+1 :  32235
N :  1
Payload :  1
true key :  11
===
i :  162
inter i :  31919
inter i+1 :  31820
N :  0
Payload :  0
true key :  1100
===
i :  164
inter i :  31722
inter i+1 :  32303
N :  2
Payload :  10
true key :  11000111
===
i :  166
inter i :  32885
inter i+1 :  33234
N :  1
Payload :  1
true key :  1100011111
===
i :  168
inter i :  33584
inter i+1 :  34764
N :  3
Payload :  010
true key :  1100011111011101
===
i :  170
inter i :  35944
inter i+1 :  36357
N :  2
Payload :  10
true key :  11000111110111010111
===
i :  172
inter i :  36771
inter i+1 :  36188
N :  2
Payload :  01
true key :  110001111101110101111101
===
i :  174
inter i :  35606
inter i+1 :  34710
N :  3
Payload :  101
true key :  110001111101110101111101110111
===
i :  176
inter i :  33814
inter i+1 :  32272
N :  4
Payload :  1000
Ganjil : 466,Genap : 466, Miss : 0, Iterasi : 932
Length of Key :  2068
Total space :  1001
32236


In [12]:
##SMOOTHING

stego_smooth = np.resize(interpolasi, (len(interpolasi)))

for i in stego_smooth:
  if i % 2 == 0 :
    stego_smooth[i] = interpolasi[i]
  else :
    stego_smooth[i] = math.ceil((interpolated[i] + interpolasi[i])/2)



In [13]:
yo = 160 

while yo < 180 :
  print("index : ", yo)
  print("interolated (double size) : ", interpolated[yo])
  print("unsmoothed (double size) : ", interpolasi[yo])
  print("smoothed : (double size) :",stego_smooth[yo])
  print("===")
  yo+=1

index :  160
interolated (double size) :  32552
unsmoothed (double size) :  32552
smoothed : (double size) : 32552
===
index :  161
interolated (double size) :  32235
unsmoothed (double size) :  32236
smoothed : (double size) : 32236
===
index :  162
interolated (double size) :  31919
unsmoothed (double size) :  31919
smoothed : (double size) : 31919
===
index :  163
interolated (double size) :  31820
unsmoothed (double size) :  31820
smoothed : (double size) : 31820
===
index :  164
interolated (double size) :  31722
unsmoothed (double size) :  31722
smoothed : (double size) : 31722
===
index :  165
interolated (double size) :  32303
unsmoothed (double size) :  32303
smoothed : (double size) : 32303
===
index :  166
interolated (double size) :  32885
unsmoothed (double size) :  32885
smoothed : (double size) : 32885
===
index :  167
interolated (double size) :  33234
unsmoothed (double size) :  33235
smoothed : (double size) : 33235
===
index :  168
interolated (double size) :  33584


In [14]:
## Step 6 - Denormalize and save Stego Audio sample
interpolasi = [x - 32768 for x in interpolasi]

### STEGOOO AS NONCHANGED SAMPLE
stegooo = np.resize(stego_smooth, (int((len(stego_smooth)+1)/2)))
for i in range(len(stegooo)):
    stegooo[i] = stego_smooth[i*2]

stego_smooth = [x - 32768 for x in stego_smooth]
print(len(stego_smooth))
print(stego_smooth)
scp.write(r'G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\smooth_interp_stego.wav', samplerate, np.array(stego_smooth, dtype=np.int16))

stego_smooth = [x + 32768 for x in stego_smooth]

### DENORMALIZE STEGOOO
stegooo = [x - 32768 for x in stegooo]
scp.write(r'G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\nonch_stego.wav', samplerate, np.array(stegooo, dtype=np.int16))

stegooo = [x + 32768 for x in stegooo]

264597
[-1403, -1192, -982, -1185, -1389, -1785, -2180, -2748, -3316, -3763, -4210, -4686, -5166, -6099, -7034, -7232, -7427, -5943, -4459, -2879, -1302, -535, 226, 416, 604, -1387, -3377, -5558, -7735, -9075, -10417, -12091, -13760, -14446, -15131, -16078, -17022, -16615, -16208, -15748, -15291, -14244, -13199, -11869, -10532, -9698, -8866, -7863, -6857, -6605, -6354, -5959, -5568, -6175, -6785, -7007, -7227, -7162, -7095, -6673, -6250, -5981, -5709, -4934, -4161, -4133, -4101, -3626, -3150, -2789, -2424, -2082, -1741, -2105, -2472, -3218, -3966, -4870, -5775, -6986, -8194, -8003, -7813, -8051, -8290, -7905, -7519, -7723, -7925, -8081, -8236, -8528, -8818, -8694, -8570, -8587, -8601, -9070, -9539, -9954, -10369, -10656, -10941, -10846, -10751, -9925, -9105, -8362, -7612, -7049, -6485, -6042, -5602, -5332, -5063, -4643, -4218, -3650, -3082, -2274, -1468, -685, 101, 900, 1702, 1011, 321, -116, -548, -1893, -3240, -3582, -3925, -2360, -794, 860, 2519, 4377, 6243, 7083, 7921, 6692, 5469, 

In [15]:
## Find PSNR value
isamplerate, iaudiodata = scp.read(r'G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\interadmod.wav')
fsamplerate, faudiodata = scp.read(r'G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\smooth_interp_stego.wav')
faudiodata = faudiodata.astype(np.int32)
faudiodata = faudiodata.astype(np.int32)

normstegodata = faudiodata.copy()
for i in range(len(normstegodata)) :
  normstegodata[i] = normstegodata[i] + 32768

print(faudiodata)

print("Length of fAudio Sample: ", len(faudiodata))

# Ensure both signals have the same length
min_length = min(len(iaudiodata), len(faudiodata))
original_audio = iaudiodata[:min_length]
reconstructed_audio = faudiodata[:min_length]

# Calculate the Mean Squared Error (MSE)
tes = (original_audio - reconstructed_audio)
mse = np.mean(tes ** 2)

# Determine the maximum possible value for the audio signal
max_possible_value = 2 ** 16

# Calculate the PSNR value
psnr_value = 10 * np.log10((max_possible_value ** 2) / mse)

pyperclip.copy(psnr_value)
print('PSNR value : ', psnr_value)

[ -1403  -1192   -982 ... -20103 -19676 -19248]
Length of fAudio Sample:  264597
PSNR value :  120.33116405911763


In [16]:
### Extracting ---------------------------------------------------------------------------------------------------------------------------
## Step 1 - Normalize stego audio
print("\nExtracting Process~~~\n")
print(normstegodata)
#normstegodata = [x + 32768 for x in faudiodata]


Extracting Process~~~

[31365 31576 31786 ... 12665 13092 13520]


In [17]:
## Step 2-1 - Divide sample between odd (changed) and even (non-changed) samples
oriSample = np.resize(stego_smooth, (int((len(stego_smooth)+1)/2)))
paySample = np.resize(stego_smooth, (int(len(stego_smooth)-((len(stego_smooth)+1)/2))))
for i in range(len(stego_smooth)):
    # Even samples (original)
    if i % 2 == 0:
        oriSample[int(i/2)] = stego_smooth[i]
    # Odd samples (payload-embedded samples)
    else:
        paySample[int((i-1)/2)] = stego_smooth[i]
oriSample = [x + 0 for x in oriSample]
paySample = [x + 0 for x in paySample]

print(normstegodata)

[31365 31576 31786 ... 12665 13092 13520]


In [18]:
## Step 2-2 - Make another sample using interpolation from the divided even sample
stegoInterpolasi = np.resize(oriSample, ((len(oriSample)*2)-1))
x = 0

for i in range(len(stegoInterpolasi)):
    if i % 2 == 0:
        stegoInterpolasi[i] = stegooo[int(i/2)]
    else:
        stegoInterpolasi[i] = math.floor((stegooo[int((i-1)/2)]+stegooo[i-x])/2)
        x+=1

yo = 160
#STEGOINTERPOLATION SAMPLE
print("STEGOINTERPOLATION SAMPLE")
while yo < 180 :
    print(stegoInterpolasi[yo])
    yo+=1


STEGOINTERPOLATION SAMPLE
32552
32235
31919
31820
31722
32303
32885
33234
33584
34764
35944
36357
36771
36188
35606
34710
33814
32272
30730
29917


In [19]:
## Step 3-1 - Save the interpolation sample and find variable C
stegoInterpolasi = [x - 32768 for x in stegoInterpolasi]
scp.write(r'G:\\My Drive\\Novice Team II\\group 1\\Dataset\\Audio\\interad-extmod.wav', samplerate, np.array(stegoInterpolasi, dtype=np.int16))
stegoDuration = len(stegoInterpolasi) / samplerate
sC = (stegoDuration * 1000)/((len(stegoInterpolasi))*2)
print("C = ", sC)

## Steps 3-2 and 4 - Extraction Process
stegoInterpolasi = [x + 32768 for x in stegoInterpolasi]
spay = ''
stegopay = ''
print(len(stegoInterpolasi))
y = 1
for z in range(len(stegoInterpolasi)-1):
    # Step 4 - Odd sample (changed sample)
    if z % 2 != 0:
        stegoInterpolasi[z] = paySample[z-y]
        y += 1
        retpay = ''
        if abs(sN) == 0 and truekey[:2] == '00':
            retpay += ''
            truekey = truekey[2:]
        for x in range(abs(sN)):
            if len(truekey) == 0:
                break
            elif truekey[:2] == '01':
                retpay += '0'
                truekey = truekey[2:]
            elif truekey[:2] == '11':
                retpay += '1'
                truekey = truekey[2:]
        reversed_pay = reverse_string(retpay)
        if z > 160 and z < 169 :
            stegopay += reversed_pay
        spay += reversed_pay
        if len(truekey) == 0:
            break
    # Step 3-2 - Even sample except last (Original)
    elif z % 2 == 0:
        sd = math.sqrt((z+1-(z+2))**2+(stegoInterpolasi[z]-stegoInterpolasi[z+1])**2)
        sN = math.floor(math.log2(sC * sd))

print("Retrieved payload sample : ",stegopay)

    


C =  0.011337868480725625
264597
Retrieved payload sample :  1101


In [20]:
# Ensure that the payload retrived and the original payload are the same
sPayload = "".join(str(x) for x in spay)
print("Length of Retrieved Payload = ", len(sPayload))
print("Retrieved Payload = ", sPayload)
print("Length of Original Payload  = ", len(payload))
print("Original Payload  = ", payload)
rpayload = sPayload[:1] + sPayload[1:len(payload)].replace('', '\t')
truepayload = payload[:1] + payload[1:].replace('', '\t')
pc = ",".join(str(x) for x in payload)

err = 0
for i in range(len(sPayload)):
    if sPayload[i] != payload[i]:
        err+=1

print("How many error = ", err)


Length of Retrieved Payload =  1000
Retrieved Payload =  1101100111011010011110111110101000011010001100011101100010101011111000101010001001111011010011101000010101011100010111000101110001010000111011010000000011000100100000111000100011101010100110110000111110110111110000100000010011000010110000010010110100111001100101110001010101111010011011111100100011100100101110111110010000110010110001000000110100110101111100100111000101100000100100101110101110100000001011100011011110011000000101111101011000110110101000010100010001010101000111011111010010011010110111100011011111110000000111110010111001110010010010101100000010101011001101011011111000111010001000001111111101111010011111010111111111001010110100000000010110100011001100100001101110111111000010000101110000101011110001100001000110101110100010000010000010000011100111010010011111101100101100101110001110100101111011100011100010010100100010000101101101010010100010010011000001110100000000001110001110011000010101000110101110000011000000111001111

In [21]:
# Save Payload
with open(r'G:\My Drive\Novice Team II\group 1\Dataset\Payload\\RetrievedPayload1mod.txt', 'w') as file:
    # Write the data to the file
    file.write(rpayload)
if sPayload[:len(payload)] == payload:
    print("Payload retrieved successfully.")
else:
    # print("Fail to get the payload.")
    raise ValueError("Fail to get the payload.")

Payload retrieved successfully.


In [22]:
print(len(stegoInterpolasi))
yo = 160
print("Extracted Sample")
while yo < 180 :
    print(stegoInterpolasi[yo])
    yo+=1

264597
Extracted Sample
32552
32236
31919
31820
31722
32303
32885
33235
33584
34763
35944
36357
36771
36188
35606
34711
33814
32270
30730
29918


In [23]:
print(len(normstegodata))
print(len(oriSample))
print("normaudiodata : ", normaudiodata)
print("normstegodata : ", normstegodata)
print("orisample : ", oriSample)
print("p_interpolasi : ", p_interpolasi)
#STEGOINTERPOLATION SAMPLE

print(len(oriSample))
yo = 80
print("ori SAMPLE")
while yo < 160 :
    print(oriSample[yo])
    yo+=1



264597
132299
normaudiodata :  [32010, 30721, 32851, 29908, 31269, 27635, 29481, 25723, 25745, 24937, 31681, 31252, 34737, 32008, 26775, 23292, 21411, 16605, 18669, 12824, 20296, 14658, 24480, 19993, 27812, 24011, 28817, 25584, 26382, 24701, 26646, 26391, 27728, 29486, 27848, 31389, 29300, 32755, 27837, 29767, 24219, 24929, 24981, 23975, 26523, 23163, 25902, 21999, 26398, 21936, 24523, 20275, 23380, 20654, 26673, 23639, 28928, 25404, 30006, 27095, 32278, 30323, 35415, 33526, 32652, 31788, 27269, 30418, 33530, 37045, 40978, 40400, 36075, 33315, 28022, 26183, 27353, 27190, 31677, 31723, 32275, 32829, 31010, 32435, 33336, 33832, 38057, 35485, 35727, 31902, 29558, 28651, 31216, 31868, 30736, 32668, 30569, 33319, 33047, 33929, 31226, 30809, 31123, 29026, 28716, 26599, 28676, 27492, 31830, 30596, 30070, 29772, 27540, 28719, 25618, 28867, 27210, 31003, 27689, 32047, 26905, 32069, 29114, 32402, 27372, 28686, 24907, 24159, 23744, 20910, 19917, 18012, 19373, 21219, 26558, 30681, 31578, 35244, 27

In [24]:
#gimana cara ngebalikin oriSample? oriSample udah sama dengan p_interpolasi, nah cara balikinnya biar balik sama kaya audiodata gimana? (simpelnya gimana cara ngereverse bagian PRE INTERPOLATION)

In [25]:
## Step 6 - Denormalize and save Original Audio sample
denormOriSample = [x - 32768 for x in oriSample]

scp.write(r'G:\My Drive\Novice Team II\group 1\Dataset\Audio\oriaud_axtmod.wav', samplerate, np.array(denormOriSample, dtype=np.int16))

In [26]:
ocsamplerate, ocaudiodata = scp.read(r'G:\My Drive\Novice Team II\group 1\Dataset\Audio\oriaud_axtmod.wav')
print("original audio data : ", ocaudiodata)
print("audiodata : ", audiodataa)
if np.array_equal(ocaudiodata, audiodataa):
    print("Cover retrieved successfully.")
else:
    print("Cover is not the same as the original.")

original audio data :  [ -1403   -982  -1389 ... -21661 -20103 -19248]
audiodata :  [-1403, -982, -1389, -2180, -3316, -4210, -5166, -7034, -7427, -4459, -1302, 226, 604, -3377, -7735, -10417, -13760, -15131, -17022, -16208, -15291, -13199, -10532, -8866, -6857, -6354, -5568, -6785, -7227, -7095, -6250, -5709, -4161, -4101, -3150, -2424, -1741, -2472, -3966, -5775, -8194, -7813, -8290, -7519, -7925, -8236, -8818, -8570, -8601, -9539, -10369, -10941, -10751, -9105, -7612, -6485, -5602, -5063, -4218, -3082, -1468, 101, 1702, 321, -548, -3240, -3925, -794, 2519, 6243, 7921, 5469, 1927, -2100, -5666, -6000, -5497, -3335, -1068, -769, -216, -849, -1046, 117, 816, 3176, 4003, 2838, 1046, -2038, -3664, -2835, -1226, -1466, -1066, -1150, -824, 415, 720, -191, -1751, -1802, -2694, -3897, -5111, -5131, -4684, -3107, -1555, -2435, -2847, -4112, -4639, -5600, -5526, -4730, -3662, -3422, -2900, -3292, -3281, -2177, -2010, -2881, -4739, -5972, -8235, -8817, -10441, -12355, -13804, -14076, -12472, -8